# UC Migration - Workflows Scope Analysis

The following is an analysis of the number of workflows that require to be migrated using system tables. This information should be combined with other sources such as UCX assessment results as well as SME meetings to account for deprecated workflows etc to come up with a final migration target.

## 1. List all jobs in workspace

Filter Names as follows:
name NOT ILIKE '%views%' and name NOT ILIKE '%test%' and name NOT LIKE '%New %' and name NOT ILIKE '%Onetime%' and name NOT ILIKE '%UCX%'

In [0]:
%sql
CREATE WIDGET TEXT WorkspaceID DEFAULT "1444828305810485";

This is a count of all the jobs in the system table - keep in mind that system tables have a default retention period of 1 year. If jobs older than that should be considered for migration, use the UCX assessment tool results to start from as a baseline.

In [0]:
%sql
SELECT DISTINCT 
    job_id AS job_id,
    workspace_id,
    name
FROM  
    system.lakeflow.jobs 
WHERE 
    workspace_id = ${WorkspaceID} 
    AND name != 'Untitled' 
    AND delete_time IS NULL 
    AND name NOT ILIKE '%views%' 
    AND name NOT ILIKE '%test%' 
    AND name NOT LIKE '%New %' 
    AND name NOT ILIKE '%Onetime%' 
    AND name NOT ILIKE '%UCX%'

job_id workspace_id name 947001688634063 1444828305810485 Omnicell_IV_Ingest 616319490052122 1444828305810485 dbdemos_lakehouse_retail_c360_init_users_scott_stafford 180595848766005 1444828305810485 Advanced MLOPS - Retraining and Deployment 100394157269037 1444828305810485 [Quality Anomaly Detection] on schema demo_ykko.dbdemos 643817008528566 1444828305810485 dbdemos_mlops_end2end_init_pat_giovannotti 6267471810525 1444828305810485 dbdemos_lakehouse_fsi_credit_pinchu_ye 214392342915821 1444828305810485 Team5-Retail-KYC-Demo 659683426819216 1444828305810485 [dev matthew_giglia] gates_demo_job 994616958924987 1444828305810485 job1 130622737650137 1444828305810485 Omnicell_OCP_Ingest 824297968432928 1444828305810485 job2 31329133383280 1444828305810485 dbdemos_lakehouse_fsi_fraud_init_erika_fonseca 320459471992303 1444828305810485 dave-ea-salesforce job 323203575127435 1444828305810485 demos_dlt_loans_init_rabi_abbasi 1005994560792671 1444828305810485 monitor_and_retrain 334895434496097 1444828305810485 dave-svls job 852037676170867 1444828305810485 nnu9 job 845298228158324 1444828305810485 [Quality Anomaly Detection] on schema dn_india.ni_nyc_taxi 947001688634063 1444828305810485 Omnicell_XL_Transactions_Ingest 915963341768319 1444828305810485 [372649807189945] Trace Metrics Computation Job 96208980748759 1444828305810485 [372649807042925] Trace Metrics Computation Job 652756218816803 1444828305810485 Google_Analytics_Ingestion job 512549897279280 1444828305810485 deploy_kandinsky_2_2_controlnet 606814746685997 1444828305810485 M2131 Firewall Pipeline 587655917635063 1444828305810485 dbdemos_billing_forecast_init_kari_ross 235574021564344 1444828305810485 nima-demo-6-5-2025 job 722588710924895 1444828305810485 [372649807149961] Trace Archive Job 1105445319333427 1444828305810485 [372649807149961] Trace Metrics Computation Job 328807347293034 1444828305810485 grant_permissions_mlendpoint_app 215478566995842 1444828305810485 [372649807189945] Trace Archive Job 939962097241703 1444828305810485 [Quality Anomaly Detection] on schema zacdav.default 1076624369929835 1444828305810485 [372649807189945] Trace Archive Job 674911967750665 1444828305810485 [dev matthew_giglia] Publish to PBI 1091556702366688 1444828305810485 deploy_kandinsky_2_2_controlnet 638535280480453 1444828305810485 SD job 130622737650137 1444828305810485 Omnicell_IV_Transactions_Ingest 1071709041068849 1444828305810485 Advanced MLOPS - Retraining and Deployment 674911967750665 1444828305810485 Publish to PBI 496416778332873 1444828305810485 Omnicell_Usage_Load 889166019843715 1444828305810485 [372649807042925] Trace Archive Job 729406762679484 1444828305810485 [372649807189945] Trace Archive Job 45273314416213 1444828305810485 [dev zach_king] sftp_ingestion_job 1006195585067944 1444828305810485 [dev firas_farah] train_register_job 707428681710419 1444828305810485 [372649807136722] Trace Metrics Computation Job 280776346609507 1444828305810485 demos_dlt_cdc_init_aravinth_kalaiselvan 736895649147217 1444828305810485 load_nyc_data 173195273960333 1444828305810485 [372649807136722] Trace Archive Job 949930095407054 1444828305810485 Clone of demos_dlt_loans_init_nada_elatlassi 2 943247015825821 1444828305810485 jovi_salesforce job 379522181141157 1444828305810485 daveok-sql-energyaustralia-ingest job 496416778332873 1444828305810485 Usage_Load 298651585267657 1444828305810485 [dev matthew_giglia] Run Synthea On DBX 619336922217651 1444828305810485 deploy_kandinsky_2_2_controlnet 1025440493138236 1444828305810485 [FEMSA] ETL_CARGA_CLIENTES_MATERIALES_MOTORES_RAP_RLP 728374398705164 1444828305810485 grant_permissions_mlendpoint_app 882395828681688 1444828305810485 Advanced MLOPS - Retraining and Deployment 271989544321980 1444828305810485 Retail_kyc_clustering_job 377612350690494 1444828305810485 [Quality Anomaly Detection] on schema mcwhorter.lakehouse_monitoring_demo 101310491221249 1444828305810485 grant_permissions_mlendpoint_app 1058348407044532 1444828305810485 [Qual

## 2. Add Created Date

We would like to infer the Created Date to use as one of the factors in determining if a workflow should be included in the migration.

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW list_of_jobs AS (
    WITH created_date AS (
        SELECT DISTINCT 
            job_id AS job_id,
            workspace_id,
            name,
            change_time,
            FIRST_VALUE(change_time) OVER (PARTITION BY job_id ORDER BY change_time ASC) AS created_date,
            FIRST_VALUE(name) OVER (PARTITION BY job_id ORDER BY change_time DESC) AS latest_name
        FROM  
            system.lakeflow.jobs 
        WHERE 
            workspace_id = ${WorkspaceID} 
            AND name != 'Untitled'
            AND delete_time IS NULL
            AND name NOT ILIKE '%views%'
            AND name NOT ILIKE '%test%'
            AND name NOT LIKE '%New %'
            AND name NOT ILIKE '%Onetime%'
            AND name NOT ILIKE '%UCX%'
    )
    SELECT DISTINCT 
        job_id,
        created_date,
        workspace_id,
        latest_name
    FROM
        created_date
)


Executing subquery: CREATE OR REPLACE TEMPORARY VIEW job_cost_analysis AS (
SELECT
  t1.usage_metadata.job_id as job_id,
  SUM(t1.usage_quantity * list_prices.pricing.default) AS list_cost
FROM system.billing.usage t1
  INNER JOIN system.billing.list_prices list_prices
    ON
      t1.cloud = list_prices.cloud AND
      t1.sku_name = list_prices.sku_name AND
      t1.usage_start_time >= list_prices.price_start_time AND
      (t1.usage_end_time <= list_prices.price_end_time or list_prices.price_end_time is NULL)
WHERE
  -- t1.workspace=
  t1.workspace_id = 1444828305810485  AND
  t1.sku_name LIKE '%JOBS%' AND
  t1.usage_metadata.job_id IS NOT NULL AND
  t1.usage_metadata.job_run_id IS NOT NULL
GROUP BY job_id
).
Executing subquery: CREATE OR REPLACE TEMPORARY VIEW Type_Job_Run AS (
  SELECT 
    DISTINCT jrt.job_id
  FROM 
    system.lakeflow.job_run_timeline AS jrt
  WHERE 
    jrt.period_start_time > '2024-01-01'
    AND (jrt.run_type = 'JOB_RUN' OR jrt.run_type IS NULL)
    AND jrt.


## 3. Count of Job Runs

Create a group by table from system.lakeflow.job_run_timeline to count how many times a job has been run over a period of time. This is another indicator of whether a workflow is relevant for migration or not. We would like to measure it through every quarter as well, to get an idea of frequency of runs through each quarter.

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW count_of_runs AS (

WITH total_runs AS (
  SELECT job_id, COUNT(*) AS Total_Runs, min(period_start_time) as earliest_execution_time , max(period_end_time) as latest_execution_time
  FROM system.lakeflow.job_run_timeline
  WHERE 
  result_state = 'SUCCEEDED'
  AND workspace_id = ${WorkspaceID} 
  AND (run_type = 'JOB_RUN' OR run_type is null)
  GROUP BY job_id
), 

q1_runs AS (
  SELECT jrt.job_id, COUNT(*) AS q1_2024_Runs, SUM(t1.usage_quantity * list_prices.pricing.default) AS q1_2024_list_cost
  FROM system.lakeflow.job_run_timeline jrt
  INNER JOIN system.billing.usage t1
  ON t1.usage_metadata.job_id = jrt.job_id IS NOT NULL AND
  t1.usage_metadata.job_run_id = jrt.run_id 
  INNER JOIN system.billing.list_prices list_prices
    ON
      t1.cloud = list_prices.cloud AND
      t1.sku_name = list_prices.sku_name AND
      t1.usage_start_time >= list_prices.price_start_time AND
      (t1.usage_end_time <= list_prices.price_end_time or list_prices.price_end_time is NULL)

  WHERE result_state = 'SUCCEEDED'
    AND jrt.period_start_time >= '2024-01-01'
    AND jrt.period_start_time < '2024-04-01'
    AND jrt.workspace_id = ${WorkspaceID} 
    AND (jrt.run_type = 'JOB_RUN' OR jrt.run_type is null)
      -- t1.workspace=
    AND t1.workspace_id = ${WorkspaceID}  
    AND t1.sku_name LIKE '%JOBS%'
  GROUP BY job_id
),

q2_runs AS (
  SELECT jrt.job_id, COUNT(*) AS q2_2024_Runs, SUM(t1.usage_quantity * list_prices.pricing.default) AS q2_2024_list_cost
  FROM system.lakeflow.job_run_timeline jrt
  INNER JOIN system.billing.usage t1
  ON t1.usage_metadata.job_id = jrt.job_id IS NOT NULL AND
  t1.usage_metadata.job_run_id = jrt.run_id 
  INNER JOIN system.billing.list_prices list_prices
    ON
      t1.cloud = list_prices.cloud AND
      t1.sku_name = list_prices.sku_name AND
      t1.usage_start_time >= list_prices.price_start_time AND
      (t1.usage_end_time <= list_prices.price_end_time or list_prices.price_end_time is NULL)

  WHERE result_state = 'SUCCEEDED'
    AND jrt.period_start_time >= '2024-04-01'
    AND jrt.period_start_time < '2024-07-01'
    AND jrt.workspace_id = ${WorkspaceID} 
    AND (jrt.run_type = 'JOB_RUN' OR jrt.run_type is null)
      -- t1.workspace=
    AND t1.workspace_id = ${WorkspaceID}  
    AND t1.sku_name LIKE '%JOBS%'
  GROUP BY job_id

),

q3_runs AS (
  SELECT jrt.job_id, COUNT(*) AS q3_2024_Runs, SUM(t1.usage_quantity * list_prices.pricing.default) AS q3_2024_list_cost
  FROM system.lakeflow.job_run_timeline jrt
  INNER JOIN system.billing.usage t1
  ON t1.usage_metadata.job_id = jrt.job_id IS NOT NULL AND
  t1.usage_metadata.job_run_id = jrt.run_id 
  INNER JOIN system.billing.list_prices list_prices
    ON
      t1.cloud = list_prices.cloud AND
      t1.sku_name = list_prices.sku_name AND
      t1.usage_start_time >= list_prices.price_start_time AND
      (t1.usage_end_time <= list_prices.price_end_time or list_prices.price_end_time is NULL)

  WHERE result_state = 'SUCCEEDED'
    AND jrt.period_start_time >= '2024-07-01'
    AND jrt.period_start_time < '2024-10-01'
    AND jrt.workspace_id = ${WorkspaceID} 
    AND (jrt.run_type = 'JOB_RUN' OR jrt.run_type is null)
      -- t1.workspace=
    AND t1.workspace_id = ${WorkspaceID}  
    AND t1.sku_name LIKE '%JOBS%'
  GROUP BY job_id
),

q4_runs AS (
  SELECT jrt.job_id, COUNT(*) AS q4_2024_Runs, SUM(t1.usage_quantity * list_prices.pricing.default) AS q4_2024_list_cost
  FROM system.lakeflow.job_run_timeline jrt
  INNER JOIN system.billing.usage t1
  ON t1.usage_metadata.job_id = jrt.job_id IS NOT NULL AND
  t1.usage_metadata.job_run_id = jrt.run_id 
  INNER JOIN system.billing.list_prices list_prices
    ON
      t1.cloud = list_prices.cloud AND
      t1.sku_name = list_prices.sku_name AND
      t1.usage_start_time >= list_prices.price_start_time AND
      (t1.usage_end_time <= list_prices.price_end_time or list_prices.price_end_time is NULL)

  WHERE result_state = 'SUCCEEDED'
    AND jrt.period_start_time >= '2024-10-01'
    AND jrt.period_start_time <= '2024-12-31'
    AND jrt.workspace_id = ${WorkspaceID} 
    AND (jrt.run_type = 'JOB_RUN' OR jrt.run_type is null)
      -- t1.workspace=
    AND t1.workspace_id = ${WorkspaceID}  
    AND t1.sku_name LIKE '%JOBS%'
  GROUP BY job_id

),

q1_2025_runs AS (
  SELECT jrt.job_id, COUNT(*) AS q1_2025_Runs, SUM(t1.usage_quantity * list_prices.pricing.default) AS q1_2025_list_cost
  FROM system.lakeflow.job_run_timeline jrt
  INNER JOIN system.billing.usage t1
  ON t1.usage_metadata.job_id = jrt.job_id IS NOT NULL AND
  t1.usage_metadata.job_run_id = jrt.run_id 
  INNER JOIN system.billing.list_prices list_prices
    ON
      t1.cloud = list_prices.cloud AND
      t1.sku_name = list_prices.sku_name AND
      t1.usage_start_time >= list_prices.price_start_time AND
      (t1.usage_end_time <= list_prices.price_end_time or list_prices.price_end_time is NULL)

  WHERE result_state = 'SUCCEEDED'
    AND jrt.period_start_time >= '2025-01-01'
    AND jrt.period_start_time < '2025-04-01'
    AND jrt.workspace_id = ${WorkspaceID} 
    AND (jrt.run_type = 'JOB_RUN' OR jrt.run_type is null)
      -- t1.workspace=
    AND t1.workspace_id = ${WorkspaceID}  
    AND t1.sku_name LIKE '%JOBS%'
  GROUP BY job_id
),

q2_2025_runs AS (
  SELECT jrt.job_id, COUNT(*) AS q2_2025_Runs, SUM(t1.usage_quantity * list_prices.pricing.default) AS q2_2025_list_cost
  FROM system.lakeflow.job_run_timeline jrt
  INNER JOIN system.billing.usage t1
  ON t1.usage_metadata.job_id = jrt.job_id IS NOT NULL AND
  t1.usage_metadata.job_run_id = jrt.run_id 
  INNER JOIN system.billing.list_prices list_prices
    ON
      t1.cloud = list_prices.cloud AND
      t1.sku_name = list_prices.sku_name AND
      t1.usage_start_time >= list_prices.price_start_time AND
      (t1.usage_end_time <= list_prices.price_end_time or list_prices.price_end_time is NULL)

  WHERE result_state = 'SUCCEEDED'
    AND jrt.period_start_time >= '2025-04-01'
    AND jrt.period_start_time < '2025-07-01'
    AND jrt.workspace_id = ${WorkspaceID} 
    AND (jrt.run_type = 'JOB_RUN' OR jrt.run_type is null)
      -- t1.workspace=
    AND t1.workspace_id = ${WorkspaceID}  
    AND t1.sku_name LIKE '%JOBS%'
  GROUP BY job_id
),

all_executions AS (

SELECT t.job_id, Total_Runs, q1_2024_Runs, q1_2024_list_cost, q2_2024_Runs, q2_2024_list_cost, q3_2024_Runs, q3_2024_list_cost, q4_2024_Runs, q4_2024_list_cost, q1_2025_Runs, q1_2025_list_cost, q2_2025_Runs, q2_2025_list_cost, earliest_execution_time, latest_execution_time
FROM total_runs t
LEFT JOIN q1_runs ON t.job_id = q1_runs.job_id
LEFT JOIN q2_runs ON t.job_id = q2_runs.job_id
LEFT JOIN q3_runs ON t.job_id = q3_runs.job_id
LEFT JOIN q4_runs ON t.job_id = q4_runs.job_id
LEFT JOIN q1_2025_runs ON t.job_id = q1_2025_runs.job_id
LEFT JOIN q2_2025_runs ON t.job_id = q2_2025_runs.job_id

)

SELECT *
FROM (
    SELECT *,
           ROW_NUMBER() OVER (PARTITION BY job_id ORDER BY latest_execution_time DESC) AS rn
    FROM all_executions
) t
WHERE t.rn = 1
)



## 4. Cost of Job Runs

Here, we aggregate the cost of a job over multiple runs. These are list prices, but they should give a comparative overview of which workloads are most expensive, and they can also serve as a prioritization metric for workflow scope.

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW job_cost_analysis AS (
SELECT
  t1.usage_metadata.job_id as job_id,
  SUM(t1.usage_quantity * list_prices.pricing.default) AS list_cost
FROM system.billing.usage t1
  INNER JOIN system.billing.list_prices list_prices
    ON
      t1.cloud = list_prices.cloud AND
      t1.sku_name = list_prices.sku_name AND
      t1.usage_start_time >= list_prices.price_start_time AND
      (t1.usage_end_time <= list_prices.price_end_time or list_prices.price_end_time is NULL)
WHERE
  -- t1.workspace=
  t1.workspace_id = ${WorkspaceID}  AND
  t1.sku_name LIKE '%JOBS%' AND
  t1.usage_metadata.job_id IS NOT NULL AND
  t1.usage_metadata.job_run_id IS NOT NULL
GROUP BY job_id
)

## 5. Accounting for Job Run Types

JOB_RUN	Standard job execution from	Jobs & Job Runs UI	/jobs and /jobs/runs endpoints	jobs, job_tasks, job_run_timeline, job_task_run_timeline

SUBMIT_RUN	One-time run via POST /jobs/runs/submit	and we can exclude this from the scope.

WORKFLOW_RUN	Run initiated from notebook workflow and these are not in the UI	Not accessible	job_run_timeline


https://learn.microsoft.com/en-us/azure/databricks/admin/system-tables/jobs#run-type

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW Type_Job_Run AS (
  SELECT 
    DISTINCT jrt.job_id
  FROM 
    system.lakeflow.job_run_timeline AS jrt
  WHERE 
    jrt.period_start_time > '2024-01-01'
    AND (jrt.run_type = 'JOB_RUN' OR jrt.run_type IS NULL)
    AND jrt.workspace_id = ${WorkspaceID} 
)

## 6. Job runs that are running in UC Shared Clusters, indicating that the jobs are already in UC


Sometimes, in many large enterprises, you may have situations where few jobs are already running on UC Shared Clusters and do not require a migration effort. We can identify those and exclude them from the overall scope by identifying if they are using UC Shared Clusters. UC Shared Clusters are the preferred cluster to migrate to, when going through a UC Migration. There a few assumptions here:

1. We are assuming even if 1 task in a job is using Shared Cluster, the whole workflow is UC compliant. Verify for your situation, if this assumption is valid, and if not, tweak the query accordingly.
2. A workflow that runs on Single User cluster may also be compliant with UC, but we are not considering it here, as that would mask other underlying tech debt such as use of RDD in the workflows etc. Hence, for the purpose of scoping, strictly only jobs running on shared clusters should be counted in scope, while single user cluster may be left as is and considered UC compliant on a case by case basis.


https://docs.databricks.com/api/workspace/clusters/get#data_security_mode

In [0]:
%sql
CREATE OR REPLACE TEMPORARY VIEW uc_job_run_compute AS (
WITH job_run_compute AS (
    SELECT 
        DISTINCT jtrt.job_id, 
        COALESCE(jrt.run_type, 'UNKNOWN') AS job_run_type,
        TRY_ELEMENT_AT(jtrt.compute_ids, 1) AS compute_id
    FROM 
        system.lakeflow.job_task_run_timeline AS jtrt
    INNER JOIN 
        system.lakeflow.job_run_timeline AS jrt
    ON 
        jtrt.job_id = jrt.job_id
        AND jtrt.job_run_id = jrt.run_id
    WHERE 
        jrt.result_state = 'SUCCEEDED'
        AND jrt.workspace_id = ${WorkspaceID} 
        AND jtrt.workspace_id = ${WorkspaceID} 
),

cluster_id_to_name AS (
    SELECT 
        request_params.cluster_name AS cluster_name, 
        GET_JSON_OBJECT(response.result, '$.cluster_id') AS cluster_id 
    FROM 
        system.access.audit
    WHERE
        service_name = 'clusters'
        AND action_name IN ('create', 'edit')
        AND request_params.data_security_mode IN ('USER_ISOLATION')
        AND workspace_id = ${WorkspaceID} 
)

SELECT 
    DISTINCT jrc.job_id, 
    jrc.job_run_type, 
    jrc.compute_id, 
    cin.cluster_id, 
    cin.cluster_name
FROM 
    job_run_compute AS jrc
INNER JOIN
    cluster_id_to_name AS cin
ON 
    cin.cluster_id = jrc.compute_id
)


Executing subquery: CREATE OR REPLACE TEMPORARY VIEW count_of_runs AS (

WITH total_runs AS (
  SELECT job_id, COUNT(*) AS Total_Runs, min(period_start_time) as earliest_execution_time , max(period_end_time) as latest_execution_time
  FROM system.lakeflow.job_run_timeline
  WHERE 
  result_state = 'SUCCEEDED'
  AND workspace_id = 1444828305810485 
  AND (run_type = 'JOB_RUN' OR run_type is null)
  GROUP BY job_id
), 

q1_runs AS (
  SELECT jrt.job_id, COUNT(*) AS q1_2024_Runs, SUM(t1.usage_quantity * list_prices.pricing.default) AS q1_2024_list_cost
  FROM system.lakeflow.job_run_timeline jrt
  INNER JOIN system.billing.usage t1
  ON t1.usage_metadata.job_id = jrt.job_id IS NOT NULL AND
  t1.usage_metadata.job_run_id = jrt.run_id 
  INNER JOIN system.billing.list_prices list_prices
    ON
      t1.cloud = list_prices.cloud AND
      t1.sku_name = list_prices.sku_name AND
      t1.usage_start_time >= list_prices.price_start_time AND
      (t1.usage_end_time <= list_prices.price_end_tim

# 7. Bringing it all together

To bring it all together, we join the overall list of jobs with the following:
- List of job run types that are in scope i.e. JOB_RUN type etc.
- Considering workflows that are already in UC i.e. using Shared Clusters (Anti Join as we want to exclude these)
- Include metrics on number of types they are run as well as their cost.


Use this as a starting point for discussion with various stakeholders for further rationalization of the scope of a UC migration.

In [0]:
%sql
SELECT 
    lj.*, 
    jca.*, 
    cor.*
FROM 
    list_of_jobs lj
INNER JOIN 
    Type_Job_Run tjr
    ON lj.job_id = tjr.job_id
LEFT JOIN 
    job_cost_analysis jca
    ON lj.job_id = jca.job_id
LEFT JOIN 
    count_of_runs cor
    ON lj.job_id = cor.job_id
LEFT ANTI JOIN 
    uc_job_run_compute ujrc
    ON lj.job_id = ujrc.job_id
ORDER BY 
    jca.list_cost DESC,  
    cor.Total_Runs DESC, 
    cor.latest_execution_time DESC

job_id created_date workspace_id latest_name job_id list_cost job_id Total_Runs q1_2024_Runs q1_2024_list_cost q2_2024_Runs q2_2024_list_cost q3_2024_Runs q3_2024_list_cost q4_2024_Runs q4_2024_list_cost q1_2025_Runs q1_2025_list_cost q2_2025_Runs q2_2025_list_cost earliest_execution_time latest_execution_time rn 344563368151628 2024-11-17T13:52:19.446Z 1444828305810485 4. taka_cookiedb_poc_v1_databricks_onlyml_wo_for_each 344563368151628 5142.505680 344563368151628 1 null null null null null null 86 1250.624525 null null null null 2024-11-21T00:41:46.284Z 2024-11-21T06:53:44.834Z 1 454751047881126 2025-06-02T07:26:45.106Z 1444828305810485 partition_processing_dynamic_20250602_072642 454751047881126 3828.441952 null null null null null null null null null null null null null null null null null 632862647577954 2024-11-19T05:17:36.872Z 1444828305810485 4. kuwano_cookiedb_poc_v1_databricks_onlyml_wo_for_each_onlypredict 632862647577954 2936.641213 632862647577954 24 null null null null null null 210 2116.307222 null null null null 2024-11-19T09:36:58.425Z 2024-12-07T08:35:57.865Z 1 53781340939412 2025-05-30T19:29:36.124Z 1444828305810485 partition_processing_dynamic_20250530_192930 53781340939412 2700.893382 null null null null null null null null null null null null null null null null null 893006274007077 2024-09-23T19:02:21.646Z 1444828305810485 Threat Detection Ingest 893006274007077 2515.868936 893006274007077 5881 null null null null 174 82.233801 2159 919.612652 2160 914.676854 1370 584.898823 2024-09-23T19:05:16.518Z 2025-05-28T00:44:34.063Z 1 454458451053823 2024-11-21T18:05:23.494Z 1444828305810485 4. kuwano_cookiedb_poc_v1_databricks_onlyml_wo_for_each_onlypredict_2 454458451053823 2022.812478 454458451053823 15 null null null null null null 144 1410.224224 null null null null 2024-11-21T18:33:48.933Z 2024-12-07T17:37:53.241Z 1 28911373290673 2024-11-22T00:11:30.481Z 1444828305810485 6. taka_cookiedb_poc_v1_databricks_onlyml_pt_cpu 28911373290673 1806.746324 28911373290673 2 null null null null null null 201 1312.041033 null null null null 2024-11-22T00:22:12.640Z 2024-11-22T15:04:37.593Z 1 214239654370622 2025-06-02T20:54:10.138Z 1444828305810485 partition_processing_dynamic_20250602_205407 214239654370622 1798.262453 null null null null null null null null null null null null null null null null null 423005687915800 2025-02-03T03:55:54.287Z 1444828305810485 [dev q_yu] pdf_ingestion_benchmark 423005687915800 1790.428940 423005687915800 69 null null null null null null null null 131 1734.514174 null null 2025-02-03T03:55:57.619Z 2025-03-02T04:03:02.953Z 1 565429930508916 2025-03-31T02:57:17.805Z 1444828305810485 [990384398394732] Trace Metrics Computation Job 565429930508916 1679.685887 565429930508916 14619 null null null null null null null null 943 44.250432 43039 1472.559387 2025-03-31T02:59:01.757Z 2025-06-05T21:10:58.828Z 1 182865668761027 2024-09-12T14:44:54.583Z 1444828305810485 incremental_agg_only 182865668761027 1663.640990 182865668761027 5685 null null null null 12506 1446.563206 null null null null null null 2024-09-12T14:48:29.132Z 2024-09-18T11:24:20.045Z 1 284192097623447 2025-01-17T15:58:23.661Z 1444828305810485 StreamingQueryListener 284192097623447 1492.223854 null null null null null null null null null null null null null null null null null 948708257741986 2025-02-24T21:40:17.786Z 1444828305810485 [dev viren_patel] TubiDeviceFirstSeenBenchmark 948708257741986 1487.962456 948708257741986 66 null null null null null null null null 55 230.653879 284 649.056077 2025-02-24T22:33:34.360Z 2025-05-07T21:43:36.789Z 1 687942445094667 2024-11-27T15:00:51.917Z 1444828305810485 6. kuwano_cookiedb_poc_v1_databricks_onlyml_pt_cpu 687942445094667 1359.689910 687942445094667 1 null null null null null null 96 634.932722 null null null null 2024-11-28T07:32:04.817Z 2024-11-28T14:18:18.428Z 1 565496842472974 2024-11-21T20:45:05.522Z 1444828305810485 5. taka_cookiedb_poc_v1_databricks_onlyml_pt 565496842472974 1268

In [0]:
%sql
CREATE OR REPLACE TABLE prashanth_subrahmanyam_catalog.uc_workflow_scoping.sample AS 
SELECT 
    lj.*, 
    jca.list_cost, 
    cor.total_runs, cor.q1_2025_runs, cor.q2_2025_runs, cor.earliest_execution_time, cor.latest_execution_time
FROM 
    list_of_jobs lj
INNER JOIN 
    Type_Job_Run tjr
    ON lj.job_id = tjr.job_id
LEFT JOIN 
    job_cost_analysis jca
    ON lj.job_id = jca.job_id
LEFT JOIN 
    count_of_runs cor
    ON lj.job_id = cor.job_id
LEFT ANTI JOIN 
    uc_job_run_compute ujrc
    ON lj.job_id = ujrc.job_id
ORDER BY 
    jca.list_cost DESC,  
    cor.Total_Runs DESC, 
    cor.latest_execution_time DESC

num_affected_rows num_inserted_rows